In [1]:
import pandas as pd
from math import sqrt
import plotly.express as px

In [2]:
def get_input_amount(spot_price, input_reserve, output_reserve):
    a = 997
    b = 1000
    I = input_reserve
    O = output_reserve
    P = spot_price
    
    input_amount = (
        sqrt(
            ((I*b - I*a)**2) + (4*P*O*I*a*b)
        ) - (I*b + I*a)
    )  / (2*a)

    return int(input_amount)

def calc_spot_price_after(row):
    if(row.event == 'TokenPurchase'):
        spot_price = row.eth_balance / row.token_balance
        return spot_price
    elif(row.event == 'EthPurchase'):
        spot_price = row.token_balance / row.eth_balance
        return spot_price

def calc_spot_price_before(row):
    if(row.event == 'TokenPurchase'):
        row = uniswap_history.iloc[row.name-1] 
        spot_price = row.eth_balance / row.token_balance
        return spot_price
    elif(row.event == 'EthPurchase'):
        row = uniswap_history.iloc[row.name-1] 
        spot_price = row.token_balance / row.eth_balance
        return spot_price

In [3]:
uniswap_history = pd.read_pickle('./uniswap_events.pickle')
uniswap_history = uniswap_history[
    ['event', 'eth_delta', 'token_delta', 'uni_delta', 'eth_balance', 'token_balance', 'UNI_supply']]

In [4]:
uniswap_history['spot_price_before'] = uniswap_history.apply(lambda row: calc_spot_price_before(row), axis=1)
uniswap_history['spot_price_after'] = uniswap_history.apply(lambda row: calc_spot_price_after(row), axis=1)
uniswap_history.dropna(inplace=True)

In [5]:
test = uniswap_history.iloc[0]
test

event                           EthPurchase
eth_delta                -25326059253325791
token_delta             5000000000000000000
uni_delta                                 0
eth_balance            29974673940746674209
token_balance        5905000000000000000000
UNI_supply             30000000000000000000
spot_price_before                   196.667
spot_price_after                        197
Name: 2, dtype: object

In [6]:
test.spot_price_after - test.spot_price_before

0.33297415254239127

In [12]:
def calc_profit(row):
#     if(row.event == 'EthPurchase'):
#         profit = (abs(row.eth_delta)*row.spot_price) / row.token_delta
#         return profit
#     elif(row.event == 'EthPurchase'):
#         profit = (abs(row.eth_delta)*row.spot_price) / row.token_delta
#         return profit
    profit = row.spot_price_after / row.spot_price_before
    return profit
        

In [13]:
uniswap_history['profit'] = uniswap_history.apply(lambda row: calc_profit(row), axis=1)
uniswap_history.dropna(inplace=True)

In [14]:
uniswap_history.describe()

spot_price_before  spot_price_after         profit
count      135609.000000     135609.000000  135609.000000
mean           94.675577         94.882698       1.002178
std           103.103517        103.337550       0.006055
min             0.002580          0.002739       1.000000
25%             0.005569          0.005576       1.000121
50%             0.008675          0.008768       1.000689
75%           179.879875        180.080934       1.002159
max           355.881269        387.522455       1.637832

In [15]:
px.histogram(uniswap_history['profit'])